<a href="https://colab.research.google.com/github/Oduks/Customer-Churn-Prediction-Using-Dceisioon-Tree/blob/main/Decision_Tree_to_Predict_Customer_Churn.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **Decision Tree to Predict Customer Churn**
**Dataset Description:**
CustomerID
Age
Gender
Tenure
Usage Frequency
Support Calls
Payment Delay
Subscription Type
Contract Length
Total Spend



**Import Libraries**

In [8]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import accuracy_score
from sklearn import tree

**READ DATA FROM CSV**

-Mount Drive to access google drive
-select the filepath and the file
-put in a dataframe

In [9]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [10]:
file_path = '/content/drive/My Drive/Colab Notebooks/customer_churn_dataset-testing-master.csv' # Replace with your file path
try:
    df = pd.read_csv(file_path)
    display(df.head())
except FileNotFoundError:
    print(f"Error: The file was not found at {file_path}")
except Exception as e:
    print(f"An error occurred: {e}")

CustomerID  Age  Gender  Tenure  Usage Frequency  Support Calls  \
0           1   22  Female      25               14              4   
1           2   41  Female      28               28              7   
2           3   47    Male      27               10              2   
3           4   35    Male       9               12              5   
4           5   53  Female      58               24              9   

   Payment Delay Subscription Type Contract Length  Total Spend  \
0             27             Basic         Monthly          598   
1             13          Standard         Monthly          584   
2             29           Premium          Annual          757   
3             17           Premium       Quarterly          232   
4              2          Standard          Annual          533   

   Last Interaction  Churn  
0                 9      1  
1                20      0  
2                21      0  
3                18      0  
4                18      0

# EDA
-Check for missing values

In [11]:
missing_values = df.isnull().sum()
missing_columns = missing_values[missing_values > 0]
print("Missing Values Summary:")
print(missing_columns)

df.info()
df.describe()

Missing Values Summary:
Series([], dtype: int64)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 64374 entries, 0 to 64373
Data columns (total 12 columns):
 #   Column             Non-Null Count  Dtype 
---  ------             --------------  ----- 
 0   CustomerID         64374 non-null  int64 
 1   Age                64374 non-null  int64 
 2   Gender             64374 non-null  object
 3   Tenure             64374 non-null  int64 
 4   Usage Frequency    64374 non-null  int64 
 5   Support Calls      64374 non-null  int64 
 6   Payment Delay      64374 non-null  int64 
 7   Subscription Type  64374 non-null  object
 8   Contract Length    64374 non-null  object
 9   Total Spend        64374 non-null  int64 
 10  Last Interaction   64374 non-null  int64 
 11  Churn              64374 non-null  int64 
dtypes: int64(9), object(3)
memory usage: 5.9+ MB


CustomerID           Age        Tenure  Usage Frequency  \
count  64374.000000  64374.000000  64374.000000     64374.000000   
mean   32187.500000     41.970982     31.994827        15.080234   
std    18583.317451     13.924911     17.098234         8.816470   
min        1.000000     18.000000      1.000000         1.000000   
25%    16094.250000     30.000000     18.000000         7.000000   
50%    32187.500000     42.000000     33.000000        15.000000   
75%    48280.750000     54.000000     47.000000        23.000000   
max    64374.000000     65.000000     60.000000        30.000000   

       Support Calls  Payment Delay   Total Spend  Last Interaction  \
count   64374.000000   64374.000000  64374.000000      64374.000000   
mean        5.400690      17.133952    541.023379         15.498850   
std         3.114005       8.852211    260.874809          8.638436   
min         0.000000       0.000000    100.000000          1.000000   
25%         3.000000      10.000000    313.000000          8.000000   
50%         6.000000      19.000000    534.000000         15.000000   
75%         8.000000      25.000000    768.000000         23.000000   
max        10.000000      30.000000   1000.000000         30.000000   

              Churn  
count  64374.000000  
mean       0.473685  
std        0.499311  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        1.000000  
max        1.000000

In [12]:
df['Contract Length'].unique()


array(['Monthly', 'Annual', 'Quarterly'], dtype=object)

Convert non-numerical values to numerical values

-Gender

-Subscription type

-Contract lenght

In [13]:
df['Gender'] = df['Gender'].str.strip().str.lower().map({'male': 1, 'female': 0})
print(df['Gender'].head())
df['Subscription Type'] = df['Subscription Type'].str.strip().str.lower().map({'basic': 0, 'standard': 1, 'premium': 2})
print(df['Subscription Type'].head())
df['Contract Length'] = df['Contract Length'].str.strip().str.lower().map({
    'monthly': 0,
    'quarterly': 1,
    'annual': 2
})
df.head()

0    0
1    0
2    1
3    1
4    0
Name: Gender, dtype: int64
0    0
1    1
2    2
3    2
4    1
Name: Subscription Type, dtype: int64


CustomerID  Age  Gender  Tenure  Usage Frequency  Support Calls  \
0           1   22       0      25               14              4   
1           2   41       0      28               28              7   
2           3   47       1      27               10              2   
3           4   35       1       9               12              5   
4           5   53       0      58               24              9   

   Payment Delay  Subscription Type  Contract Length  Total Spend  \
0             27                  0                0          598   
1             13                  1                0          584   
2             29                  2                2          757   
3             17                  2                1          232   
4              2                  1                2          533   

   Last Interaction  Churn  
0                 9      1  
1                20      0  
2                21      0  
3                18      0  
4                18      0

In [14]:
# Splitting the dataset into features and target variable
# Features include CustomerID, age, Gendere, Tenure etc
# The target variable is churn (0 or 1)

X = df[['Age',	'Gender',	'Tenure',	'Usage Frequency',	'Support Calls',	'Payment Delay',	'Subscription Type',	'Contract Length',	'Total Spend',	'Last Interaction']]
y = df['Churn']


#split into training and testing data, 70% to train and 30% to test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

#Train the decision tree classifier
CLF = DecisionTreeClassifier()
CLF.fit(X_train, y_train)

# Making predictions on the test set
y_pred = CLF.predict(X_test)

# Evaluating the model using accuracy
# Accuracy is the proportion of correct predictions among the total number of cases processed
accuracy = accuracy_score(y_test, y_pred)
print(f"Accuracy: {accuracy}")

# Visualizing the decision tree
# This visualization helps in understanding how the model makes decisions
plt.figure(figsize=(200, 100))
tree.plot_tree(CLF, filled = True, feature_names = ['Age',	'Gender',	'Tenure',	'Usage Frequency',	'Support Calls',	'Payment Delay',	'Subscription Type',	'Contract Length',	'Total Spend',	'Last Interaction'], class_names = ['No Churn', 'Churn'])
plt.title('Decision Tree for Predicting Customer Churn')
plt.show()



Accuracy: 0.9987055351317765
